In [1]:
import numpy as np
import pandas as pd

In [2]:
train=pd.read_json("D:/Downloads/DROP/drop_dataset/train.json")

In [5]:
train.transpose().head()

passage  \
nfl_2201      To start the season, the Lions traveled south ...   
nfl_478       Trying to snap a two-game skid, the Bills flew...   
history_690   The French king, John II, had been held captiv...   
history_2184  As of the census of 2000, there were 218,590 p...   
history_1328  From 1231, Goryeo was intermittently invaded b...   

                                                       qa_pairs  \
nfl_2201      [{'question': 'How many points did the buccane...   
nfl_478       [{'question': 'How many games had the Bills wo...   
history_690   [{'question': 'How many years before Navarrase...   
history_2184  [{'question': 'How many more people were there...   
history_1328  [{'question': 'What happened first: intermitte...   

                                                       wiki_url  
nfl_2201      https://en.wikipedia.org/wiki/2014_Cleveland_B...  
nfl_478       https://en.wikipedia.org/wiki/2014_Cleveland_B...  
history_690   https://en.wikipedia.org/wiki/2014_Cleveland_B...  
history_2184  https://en.wikipedia.org/wiki/2014_Cleveland_B...  
history_1328  https://en.wikipedia.org/wiki/2014_Cleveland_B...

In [3]:
### Get the unique ids for each contex

In [55]:
l=[]
import json
from pandas.io.json import json_normalize
with open('D:/Downloads/DROP/drop_dataset/train.json') as fh:
    data = json.load(fh)

for each in data:
    l.append(each)

In [54]:
l=[]
import json
from pandas.io.json import json_normalize
with open('D:/Downloads/DROP/drop_dataset/dev.json') as fh:
    data = json.load(fh)

for each in data:
    l.append(each)

In [16]:
### Create the dataframe for passages

In [5]:
pas=[]
code=[]
for each in l:
    pas.append(data[each]['passage'])
    code.append(each)

In [6]:
train_df=pd.DataFrame()

In [7]:
train_df['passage']=pd.Series(pas)
train_df['code']=pd.Series(code)

In [8]:
train_df.head()

passage          code
0  To start the season, the Lions traveled south ...      nfl_2201
1  Trying to snap a two-game skid, the Bills flew...       nfl_478
2  The French king, John II, had been held captiv...   history_690
3  As of the census of 2000, there were 218,590 p...  history_2184
4  From 1231, Goryeo was intermittently invaded b...  history_1328

In [60]:
import nltk
nltk.download('punkt')
def tokenize(sequence):
    tokens = [token.replace("``", '"').replace("''", '"') for token in nltk.word_tokenize(sequence)]
    return [x for x in tokens] 

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\User\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


#### Tokenize function

In [10]:
file=open("train_context.txt","w",encoding="utf-8")
for index,row in train_df.iterrows():
    pas=tokenize(row['passage'])
    file.write(' '.join(pas)+'\n')

In [203]:
data

{'nfl_2201': {'passage': "To start the season, the Lions traveled south to Tampa, Florida to take on the Tampa Bay Buccaneers. The Lions scored first in the first quarter with a 23-yard field goal by Jason Hanson. The Buccaneers tied it up with a 38-yard field goal by Connor Barth, then took the lead when Aqib Talib intercepted a pass from Matthew Stafford and ran it in 28 yards. The Lions responded with a 28-yard field goal. In the second quarter, Detroit took the lead with a 36-yard touchdown catch by Calvin Johnson, and later added more points when Tony Scheffler caught an 11-yard TD pass. Tampa Bay responded with a 31-yard field goal just before halftime. The second half was relatively quiet, with each team only scoring one touchdown. First, Detroit's Calvin Johnson caught a 1-yard pass in the third quarter. The game's final points came when Mike Williams of Tampa Bay caught a 5-yard pass.  The Lions won their regular season opener for the first time since 2007",
  'qa_pairs': [{'q

#### Dataframe for questions and answers

In [17]:
ques=[]
code=[]
for each in l:
    for i in data[each]['qa_pairs']:
        ques.append(i['question'])
        code.append(each)

In [18]:
ans=[]
code=[]
ques=[]
for each in l:
    for i in data[each]['qa_pairs']:
        ques.append(i['question'])
        if i['answer']['number']!='':
            ans.append(i['answer']['number'])
        elif i['answer']['spans']!=[]:
            ans.append(i['answer']['spans'][-1])
        else:
            ans.append(i['answer']['date']['day']+"-"+i['answer']['date']['month']+"-"+i['answer']['date']['year'])
        code.append(each)
di={}
di['question']=ques
di['code']=code
di['answer']=ans
ans_df=pd.DataFrame(di)
ans_df.head()


question      code          answer
0  How many points did the buccaneers need to tie...  nfl_2201               3
1          How many field goals did the Lions score?  nfl_2201               2
2        How long was the Lion's longest field goal?  nfl_2201         28-yard
3      Who caught the touchdown for the fewest yard?  nfl_2201   Mike Williams
4            Who caught the shortest touchdown pass?  nfl_2201  Calvin Johnson

In [19]:
di={}
di['question']=ques
di['code']=code

In [20]:
ques_df=pd.DataFrame(di)

In [21]:
ques_df.head()

question      code
0  How many points did the buccaneers need to tie...  nfl_2201
1          How many field goals did the Lions score?  nfl_2201
2        How long was the Lion's longest field goal?  nfl_2201
3      Who caught the touchdown for the fewest yard?  nfl_2201
4            Who caught the shortest touchdown pass?  nfl_2201

#### Create files for the question and answer

In [22]:
file=open("train_question.txt","w",encoding="utf-8")
for index,row in ques_df.iterrows():
    pas=tokenize(row['question'])
    file.write(' '.join(pas)+'\n')

In [23]:
file=open("train_answer.txt","w",encoding="utf-8")
for index,row in ans_df.iterrows():
    pas=row['answer']
    file.write(pas+'\n')

In [24]:
import os
import codecs
token_filenames=['train_context.txt','train_question.txt','train_answer.txt']
data_path='C:/Users/User/'

In [25]:
lines=""
for f in token_filenames:
    file_pat  = os.path.join(data_path, f)
    read_file = codecs.open(file_pat, "r", encoding="utf-8")
    lines = lines + " " + read_file.read()
    lines = lines.lower()

#### Create Vocab

In [26]:
import re
vocab_freq=0
vocab_size=30000
from collections import Counter
words = re.findall(r'\w+', lines.lower())
#words.remove('1')
temp_vocab = Counter(words)
if vocab_freq == 0:
    vocab_words = temp_vocab.most_common(vocab_size)
else:
    vocab_words = []
    for i in temp_vocab:
        if (temp_vocab[i] > vocab_freq):
            vocab_words.append([i, temp_vocab[i]])

    print ("Vocab size is ", len(vocab_words))

In [27]:
word_to_index = {}
word_to_index["<pad>"] = 0
word_to_index["<unk>"] = 1

In [28]:
temp_index = 2
for word in vocab_words:
    if word[0] not in word_to_index:
        word_to_index[word[0]] = temp_index
        temp_index += 1


In [29]:
vocab_size = len(word_to_index)
index_to_word =  {v: k for k, v in word_to_index.items()}

In [30]:
import string
characters = {}
chars = list(string.printable.lower())
chars.remove(' ')
char_ind = 1
for c in chars:
    if c not in characters:
        characters[c] = char_ind
        char_ind += 1
char_to_index = characters
index_to_char = {v: k for k,v in char_to_index.items()}

In [31]:
### Dictionary file

In [32]:
import _pickle as cPickle
dict_all = {"word" : word_to_index, "char" : char_to_index}
cPickle.dump(dict_all, open(os.path.join(data_path, "dictionaries.pkl"), "wb"))

In [33]:
def encode_word(word):
    if word in word_to_index:
        return word_to_index[word]
    else:
        return word_to_index["<unk>"]

def encode_char(index):
    if index in index_to_char:
        return index_to_char[index]
    else:
        return "<unk>"

### Encode Questions

In [43]:
### Encode Answers

In [62]:
def encodewords(ty,dataset):
    lines=""
    file_pat  = os.path.join(data_path, dataset+'_'+ty+'.txt')
    read_file = codecs.open(file_pat, "r", encoding="utf-8")
    lines =read_file.read()
    lines=lines.split("\n")
    en=[]
    for line in lines:
        w=""
        line=line.lower()
        words=line.split()
        for word in words:
            a=encode_word(word)
            w=w+str(a)+" "
        en.append(w)
        print(en)
    cPickle.dump(en, open(os.path.join(data_path, dataset+"_encode_"+ty+".pkl"), "wb"))

In [66]:
encodewords("context","train")
encodewords("answer","train")
encodewords("question","train")

### Create embedding matrix

In [45]:
from tokenize import tokenize
embeddings_index = dict()
vocabulary_size=30000
f = open('D:/Downloads/glove6b100dtxt/glove.6B.100d.txt',encoding="utf8")
for line in f:
    values = line.split()
    word = values[0]
    coefs = np.asarray(values[1:], dtype='float32')
    embeddings_index[word] = coefs
f.close()
embedding_matrix = np.zeros((vocabulary_size, 100))
for word, index in word_to_index.items():
    if index > vocabulary_size - 1:
        break
    else:
        embedding_vector = embeddings_index.get(word)
        if embedding_vector is not None:
            embedding_matrix[index] = embedding_vector

In [35]:
embedding_matrix

array([[ 0.        ,  0.        ,  0.        , ...,  0.        ,
         0.        ,  0.        ],
       [ 0.        ,  0.        ,  0.        , ...,  0.        ,
         0.        ,  0.        ],
       [-0.038194  , -0.24487001,  0.72812003, ..., -0.1459    ,
         0.82779998,  0.27061999],
       ...,
       [ 0.        ,  0.        ,  0.        , ...,  0.        ,
         0.        ,  0.        ],
       [-0.50470001,  0.095251  ,  0.11615   , ..., -0.29440999,
        -0.19118001,  0.29644001],
       [-0.48554   ,  0.044884  ,  0.93818998, ...,  0.51103997,
        -0.43900001,  0.060774  ]])

In [36]:
word_to_index

{'<pad>': 0,
 '<unk>': 1,
 'the': 2,
 'in': 3,
 'of': 4,
 'how': 5,
 'many': 6,
 'to': 7,
 'a': 8,
 'and': 9,
 'was': 10,
 'did': 11,
 'yard': 12,
 'field': 13,
 'were': 14,
 'with': 15,
 'yards': 16,
 'first': 17,
 'touchdown': 18,
 'which': 19,
 'for': 20,
 'on': 21,
 'game': 22,
 'by': 23,
 'goal': 24,
 'quarter': 25,
 'or': 26,
 'pass': 27,
 '2': 28,
 's': 29,
 'from': 30,
 'more': 31,
 '1': 32,
 '3': 33,
 'as': 34,
 'scored': 35,
 'second': 36,
 'at': 37,
 'who': 38,
 'points': 39,
 'their': 40,
 'after': 41,
 'than': 42,
 'had': 43,
 'longest': 44,
 'years': 45,
 'goals': 46,
 'half': 47,
 'td': 48,
 'what': 49,
 'his': 50,
 'lead': 51,
 '4': 52,
 'touchdowns': 53,
 '5': 54,
 '7': 55,
 'two': 56,
 'an': 57,
 'score': 58,
 'percent': 59,
 'have': 60,
 'people': 61,
 'it': 62,
 '6': 63,
 'not': 64,
 'run': 65,
 'total': 66,
 'is': 67,
 'that': 68,
 'but': 69,
 '10': 70,
 'team': 71,
 'third': 72,
 '0': 73,
 'over': 74,
 'would': 75,
 'between': 76,
 'win': 77,
 'there': 78,
 'when'

#### PAd the Encoded the context, answer and queries

In [47]:
mean=213
std=127
ma=mean+2*std

In [34]:
with open(os.path.join(data_path, "encode_question.pkl"), "rb") as file:
    e = cPickle.load(file)
e.pop()
n=[]
for i in e:
    i=i.split()
    i=np.pad(i, (0,ma), 'constant', constant_values=(0))
    new = "" 
    for x in i: 
        new += x+" " 
    n.append(new)
    
cPickle.dump(n, open(os.path.join(data_path, "encode_pad_question.pkl"), "wb"))  


In [35]:
with open(os.path.join(data_path, "encode_answer.pkl"), "rb") as file:
    e = cPickle.load(file)
e.pop()
n=[]
for i in e:
    i=i.split()
    i=np.pad(i, (0,ma), 'constant', constant_values=(0))
    new = "" 
    for x in i: 
        new += x+" " 
    n.append(new)
    
cPickle.dump(n, open(os.path.join(data_path, "encode_pad_answer.pkl"), "wb"))   

In [69]:
def pad_sequences(ty,dataset):
    with open(os.path.join(data_path, dataset+"_encode_"+ty+".pkl"), "rb") as file:
        e = cPickle.load(file)
    e.pop()
    n=[]
    for i in e:
        i=i.split()
        i=np.pad(i, (0,ma), 'constant', constant_values=(0))
        new = "" 
        for x in i: 
            new += x+" " 
        n.append(new)
    
    cPickle.dump(n, open(os.path.join(data_path, dataset+"_encode_pad_"+ty+".pkl"), "wb"))   

In [70]:
pad_sequences("answer","train")
pad_sequences("question","train")
pad_sequences("context","train")

## Validation dataset

In [57]:
l=[]
import json
from pandas.io.json import json_normalize
with open('D:/Downloads/DROP/drop_dataset/dev.json') as fh:
    data = json.load(fh)
for each in data:
    l.append(each)
pas=[]
code=[]
for each in l:
    pas.append(data[each]['passage'])
    code.append(each)
valid_df=pd.DataFrame()
valid_df['passage']=pd.Series(pas)
valid_df['code']=pd.Series(code)
valid_df.head()

passage         code
0   Hoping to rebound from their loss to the Patr...     nfl_1184
1   Still searching for their first win, the Beng...      nfl_995
2   Coming off their road loss to Green Bay, Wash...     nfl_2684
3  In 1085, Guadalajara was retaken by the Christ...  history_655
4   Trying to snap a six-game losing skid, the Li...      nfl_153

In [58]:
ans=[]
code=[]
ques=[]
for each in l:
    for i in data[each]['qa_pairs']:
        ques.append(i['question'])
        if i['answer']['number']!='':    ###If the answer is a number
            ans.append(i['answer']['number'])
        elif i['answer']['spans']!=[]:   ###If the answer is a sentence
            ans.append(i['answer']['spans'][-1])
        else:                            ###If the answer is a date
            ans.append(i['answer']['date']['day']+"-"+i['answer']['date']['month']+"-"+i['answer']['date']['year'])
        code.append(each)
di={}
di['question']=ques
di['code']=code
di['answer']=ans
ans_df=pd.DataFrame(di)
ans_df.head()

question      code         answer
0        Who scored the first touchdown of the game?  nfl_1184  Chaz Schilens
1          How many field goals did Kris Brown kick?  nfl_1184              3
2                           Which team won the game?  nfl_1184        Raiders
3  How many field goals did both teams kick in th...  nfl_1184              2
4  How many more yards was Kris Browns's first fi...  nfl_1184             29

#### Create the respective context, answer , queries files

In [61]:
file=open("valid_context.txt","w",encoding="utf-8")
for index,row in valid_df.iterrows():
    pas=tokenize(row['passage'])
    file.write(' '.join(pas)+'\n')
    
    
file=open("valid_question.txt","w",encoding="utf-8")
for index,row in ans_df.iterrows():
    pas=tokenize(row['question'])
    file.write(' '.join(pas)+'\n')


file=open("valid_answer.txt","w",encoding="utf-8")
for index,row in ans_df.iterrows():
    pas=row['answer']
    file.write(pas+'\n')

#### Encode Validation set

In [67]:
encodewords("context","valid")
encodewords("question","valid")
encodewords("answer","valid")

#### Pad Validation

In [71]:
pad_sequences("answer","valid")
pad_sequences("question","valid")
pad_sequences("context","valid")